# Model Training - LR/CNN/BiGRU/CAML


In this notebook, i'll first or load the word2vec model before moving on to train the different models such LR/CNN/GRU/CAML using the MIMIC-III dataset. Due to time limitations, the models were not hyper-parameter tuned and they were not implemented from scratch so it is alot of stitching here and there. 

In [1]:
import gensim

/home/yaolong/anaconda3/lib/python3.8/site-packages/gensim/similarities/__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)


In [2]:
#!pip install gensim

We load our trained word2vec.

In [3]:
#training_corpus = clinical_notes_df.TEXT_prop

import gensim.models.word2vec as w2v

#model = w2v.Word2Vec(vector_size=100, min_count=0, workers=20)
    
#model.build_vocab(training_corpus)
#model.train(training_corpus, total_examples=model.corpus_count, epochs=5)
#model.save('w2v_embeddings.w2v')
w2v_model = gensim.models.Word2Vec.load('w2v_embeddings.w2v')

There are actually 150,853 keys in the word2vec embedding.

In [4]:
len(w2v_model.wv.key_to_index)

150853

Just to check on the key_to_index pairs in the dictionary.

In [25]:
w2v_model.wv.key_to_index

{'the': 0,
 'and': 1,
 'to': 2,
 'of': 3,
 'was': 4,
 'with': 5,
 'a': 6,
 'on': 7,
 'in': 8,
 'for': 9,
 'no': 10,
 'mg': 11,
 'tablet': 12,
 'patient': 13,
 'is': 14,
 'he': 15,
 'at': 16,
 'blood': 17,
 'name': 18,
 'po': 19,
 'she': 20,
 'discharge': 21,
 'or': 22,
 's': 23,
 'as': 24,
 'day': 25,
 'daily': 26,
 'sig': 27,
 'one': 28,
 'his': 29,
 'left': 30,
 'last': 31,
 'history': 32,
 'her': 33,
 'were': 34,
 'right': 35,
 'by': 36,
 'had': 37,
 'be': 38,
 'this': 39,
 'admission': 40,
 'not': 41,
 'date': 42,
 'you': 43,
 'pt': 44,
 'pain': 45,
 'hospital': 46,
 'normal': 47,
 'your': 48,
 'an': 49,
 'that': 50,
 'first': 51,
 'from': 52,
 'p': 53,
 'there': 54,
 'has': 55,
 'are': 56,
 'ct': 57,
 'have': 58,
 'which': 59,
 'medications': 60,
 'but': 61,
 'up': 62,
 'chest': 63,
 'c': 64,
 'hospital1': 65,
 'd': 66,
 'hours': 67,
 'times': 68,
 'o': 69,
 'well': 70,
 'status': 71,
 'time': 72,
 'dr': 73,
 'also': 74,
 'home': 75,
 'please': 76,
 'given': 77,
 'stable': 78,
 'c

We observe from the shape of the word2vec vector that the embedding size is 100. There are more than 150,853 words in the vocabulary.

In [26]:
w2v_model.wv.vectors.shape

(150853, 100)

These are the embeddings for words in the word2vec model.

In [27]:
w2v_model.wv.vectors

array([[ 1.5468743e+00, -1.3960623e+00, -1.5605626e-01, ...,
        -1.6178794e+00, -3.0033451e-01,  3.2768281e+00],
       [ 2.2256966e+00, -7.1249175e-01, -2.7485168e-01, ...,
        -5.0227606e-01, -3.1828463e-01, -1.0110099e+00],
       [ 1.0349745e+00,  2.7597139e+00, -5.0118904e+00, ...,
         5.3436011e-01,  4.3702689e-01, -1.8575033e+00],
       ...,
       [-1.8613907e-02,  6.2861880e-03, -3.8976893e-03, ...,
        -5.6359936e-03, -6.7960252e-03, -1.7990358e-02],
       [-4.8878398e-02,  4.9264722e-02, -2.6864210e-02, ...,
        -3.6684349e-02, -2.2577880e-02, -1.2140578e-02],
       [-5.4648016e-03,  2.5473697e-02,  2.7994996e-02, ...,
        -1.1924580e-02, -1.6955193e-02,  2.9692452e-02]], dtype=float32)

ICD9 descriptions from WHO was not used in this work. It can be used if needed and can be safely omitted.

In [28]:
#icd9_descriptions = pd.read_csv('ICD9_descriptions', sep='\t')
#icd9_descripddtions.head()

@                                ICD9 Hierarchy Root
0        00  Procedures and interventions, Not Elsewhere Cl...
1  00-99.99                                         PROCEDURES
2      00.0                             Therapeutic ultrasound
3     00.01  Therapeutic ultrasound of vessels of head and ...
4     00.02                    Therapeutic ultrasound of heart

We combine the procedure and diagnoses medical codes using a left join on admission ID.

In [29]:
codes_with_notes = pd.merge(combined_codes, clinical_notes_df, on='HADM_ID', how='left')
#codes_with_notes_and_desc = pd.merge(codes_with_notes, icd9_descriptions, how='left', left_on='full_code', right_on='@')
codes_with_notes = codes_with_notes[codes_with_notes['TEXT_prop'].notna()]
codes_with_notes.head()
#del combined_codes, clinical_notes_df, codes_with_notes, icd9_descriptions

ROW_ID_x  SUBJECT_ID_x  HADM_ID  SEQ_NUM ICD9_CODE tmp_code  \
0      1297           109   172335      1.0     40301   403.01   
1      1311           109   173633      1.0     40301   403.01   
2      1488           112   174105      1.0     53100   531.00   
3      1493           113   109976      1.0      1915    191.5   
4      1496           114   178393      1.0     41401   414.01   

                                           full_code  ROW_ID_y  SUBJECT_ID_y  \
0  403.01;486;582.81;585.5;425.4;276.2;710.0;276....   14797.0         109.0   
1  403.01;585.6;583.81;710.0;558.9;287.5;285.21;4...   14801.0         109.0   
2   531.00;410.71;285.9;414.01;725;44.43;99.04;45.13   54002.0         112.0   
3                       191.5;331.4;530.81;15.9;23.9   10256.0         113.0   
4  414.01;411.1;482.83;285.9;272.0;305.1;36.12;36...   10754.0         114.0   

    CHARTDATE CHARTTIME STORETIME           CATEGORY DESCRIPTION  CGID  \
0  2141-09-24       NaN       NaN  Discharge summary      Report   NaN   
1  2141-12-14       NaN       NaN  Discharge summary      Report   NaN   
2  2194-06-18       NaN       NaN  Discharge summary      Report   NaN   
3  2140-12-27       NaN       NaN  Discharge summary      Report   NaN   
4  2146-09-03       NaN       NaN  Discharge summary      Report   NaN   

   ISERROR                                               TEXT  \
0      NaN  Admission Date:  [**2141-9-18**]              ...   
1      NaN  Admission Date:  [**2141-12-8**]              ...   
2      NaN  Admission Date: [**2194-6-13**]        Dischar...   
3      NaN  Admission Date: [**2140-12-12**]        Discha...   
4      NaN  Admission Date:  [**2146-8-29**]       Dischar...   

                                           TEXT_prop  
0  [admission, date, discharge, date, date, of, b...  
1  [admission, date, discharge, date, date, of, b...  
2  [admission, date, discharge, date, service, hi...  
3  [admission, date, discharge, date, date, of, b...  
4  [admission, date, discharge, date, date, of, b...

We perform a train-test split of our dataset.

In [30]:
from sklearn.model_selection import train_test_split

#X, X_test, y, y_test = train_test_split(codes_with_notes[['SUBJECT_ID_x','HADM_ID','TEXT_prop']], codes_with_notes['full_code'], test_size=0.2, random_state=42)
#X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.25, random_state=42)

X_train, X_val, y_train, y_val = train_test_split(codes_with_notes[['SUBJECT_ID_x','HADM_ID','TEXT_prop']], codes_with_notes['full_code'], test_size=0.2, random_state=42)

We make use of the following utility function to obtain the index to word and word to index.

In [31]:
# Reference: https://github.com/jamesmullenbach/caml-mimic
def get_words_to_indexes_dictionaries(embed_file):
    """
    Create a vocabulary from the embeddings file and for every word create and corresponding index and vice versa
    :param embed_file: The file with the embeddings words
    :return: Two dictionaries
    """
    #df = pd.read_csv(embed_file)
    ind2w = {idx + 1: word for word, idx in embed_file.items()}
    w2ind = {w: i for i, w in ind2w.items()}  # Start from 1 index. 0 index will represent the padding weights
    return ind2w, w2ind

We obtain the index to word and word to index vectors

In [32]:
ind2w, w2ind = get_words_to_indexes_dictionaries(w2v_model.wv.key_to_index)

We make use of the following utility function to obtain the index to code and code to index. 

In [35]:
from collections import defaultdict

# Reference: https://github.com/jamesmullenbach/caml-mimic
def load_full_codes(full_codes):

    codes = set()
    #print(full_codes)
    for line in full_codes:
        for code in line.split(';'):
        #print(code)
            codes.add(code)
    codes = set([c for c in codes if c != ''])
    ind2c = defaultdict(str, {i: c for i, c in enumerate(sorted(codes))})
    c2ind = {c: i for i, c in ind2c.items()}
    return ind2c, c2ind

# Compute dictionary with index to code  and vice versa along with code descriptions
ind2c, c2ind = load_full_codes(codes_with_notes['full_code'])

The following class implementation of WordsWithLabelDataset is very similar to James Mullenback's implementation. 

In [38]:
from torch.utils.data import TensorDataset, Dataset
import numpy as np
import torch

# Very similar to James Mullenbach's implementation, I had to change it a little to make it work.
class WordsWithLabelDataset(Dataset):
    def __init__(self, df, c2ind_dict, w2ind_dict):
        self.num_labels = len(c2ind_dict)
        self.labels = []
        self.docs = []
        self.max_length = 2500  # max words in a document
        for index, row in df.iterrows():
            # Create label vector
            labels_idx = np.zeros(self.num_labels)
            found_at_least_one_label = False
            for l in row['full_code'].split(';'):
                if l in c2ind_dict.keys():
                    code = int(c2ind_dict[l])
                    labels_idx[code] = 1
                    found_at_least_one_label = True
            if not found_at_least_one_label:
                continue
            # Add labels_idx to labels
            self.labels.append(labels_idx)
            # Convert words to indexes. If a word is not in embeddings it is considered unknown and the corresponding it is length of embedding words +1.
            # This index in the embeddings weight matrix is a random vector (Gaussian)
            text = [int(w2ind_dict[w]) if w in w2ind_dict else len(w2ind_dict) + 1 for w in row['TEXT_prop']]
            # Truncate document
            if len(text) > self.max_length:
                text = text[:self.max_length]
            # Add docs to text
            text = np.array(text).astype(np.int)
            self.docs.append(text)

        # Convert labels to numpy
        self.labels = np.array(self.labels).astype(np.int)

    def __len__(self):
        return len(self.labels)

    def __getitem__(self, index):
        # returns will be wrapped as List of Tensor(s) by DataLoader
        return self.docs[index], self.labels[index]


# Referenced from one of the HWs. 
def visit_collate_fn(batch):
    """
    DataLoaderIter call - self.collate_fn([self.dataset[i] for i in indices])
    Thus, 'batch' is a list [(doc1, labels-one-hot encoded), (doc2, labels-one-hot encoded), ... , (docN, labelsN-one-hot encoded)]
    where N is minibatch size, doc is a (Sparse)FloatTensor, and label is a LongTensor

    :returns
        seqs (LongTensor) - 2D of batch_size X max doc length of batch
        labels (LongTensor) - 2D of batch_size. Each row represents a doc. Each column represents a label.
    """
    batch_size = len(batch)
    indices = np.arange(batch_size)
    doc_max_length = batch[0][0].size
    labels_length = batch[0][1].size
    lengths = np.zeros(batch_size).astype(int)

    for i, (doc, labels) in enumerate(batch):
        length = doc.size
        lengths[i] = length
        if length > doc_max_length:
            doc_max_length = length

    sorted_indices = [x for _, x in sorted(zip(lengths, indices), reverse=True)]
    sorted_labels = np.zeros((batch_size, labels_length), dtype=int)
    sorted_docs = np.zeros((batch_size, doc_max_length), dtype=int)

    for i, indice in enumerate(sorted_indices):
        element = batch[indice]
        doc = element[0]
        doc_length = doc.size
        label = element[1]
        sorted_labels[i] = label
        sorted_docs[i, 0:doc_length] = doc[np.newaxis, :]

    docs_tensor = torch.LongTensor(sorted_docs)
    labels_tensor = torch.FloatTensor(sorted_labels)

    return docs_tensor, labels_tensor

We check the training data and observe that the TEXT_prop column need to be converted to a string.

In [40]:
X_train.head()

SUBJECT_ID_x  HADM_ID  \
17973         12971   186975   
30018         23056   149084   
33691         25872   142428   
43722         47848   131011   
12960          9855   168096   

                                               TEXT_prop  
17973  [date, of, admission, date, of, death, date, o...  
30018  [admission, date, discharge, date, date, of, b...  
33691  [admission, date, discharge, date, date, of, b...  
43722  [admission, date, discharge, date, date, of, b...  
12960  [admission, date, discharge, date, service, ne...

We see that the target labels/medical codes are in proper format, separated by semi-colons.

In [41]:
pd.DataFrame(y_train).head()

full_code
17973  V30.00;770.84;746.89;775.7;425.3;584.9;775.5;2...
30018  200.20;996.81;518.5;584.5;286.6;570;998.11;998...
33691  V30.00;770.82;774.2;779.3;765.18;765.27;779.81...
43722             805.01;805.02;805.05;E828.2;29.4;93.41
12960      431;453.40;599.0;V10.3;593.2;38.7;38.93;88.65

We create our train and validation dataset using the WordswithLabelDataset specified earlier.

In [42]:
train_dataset = WordsWithLabelDataset(pd.concat([X_train, y_train], axis=1), c2ind, w2ind)

In [43]:
valid_dataset = WordsWithLabelDataset(pd.concat([X_val, y_val], axis=1), c2ind, w2ind)

We make use of Pytorch's build-in DataLoader function to create our train and validation loaders since we'll be using Pytorch's neural network implementation.

In [45]:
from torch.utils.data import DataLoader

train_loader = DataLoader(dataset=train_dataset, batch_size=1, shuffle=True, collate_fn=visit_collate_fn,
                              num_workers=20)

In [46]:
valid_loader = DataLoader(dataset=valid_dataset, batch_size=1, shuffle=False, collate_fn=visit_collate_fn,
                              num_workers=20)

The following utility function will zero-pad the input as well as handle words that are not in the dictionary.

In [52]:
# referenced from James Mullenbach but modified to my liking. 
def load_embeddings(W):
    """
    Add one vector for zero padding 
    Add one vector for UNK token for unknown words
    :param W: the embedding vectors
    :return W: np matrix with vectors normalized
    """
    # Create a row to represent pad vector (all zeros)
    padrow = np.array(np.zeros(len(W[-1]))).astype(np.float)
    # Place it at first position
    W = np.insert(W, 0, padrow, axis=0)
    # Create a row to represent UNK token vector (random: Gaussian)
    unkrow = np.array(np.random.randn(len(W[-1]))).astype(np.float)
    # Place it last
    W = np.vstack((W, unkrow))
    # Normalize every row and add a small number to avoid division by zero
    norm2 = (np.linalg.norm(W, axis=1) + 1e-6).astype(np.float)
    W = W / norm2[:, np.newaxis]
    
    return W

The following are the model implementations from (James Mullenbach, 2018) and I had to change my inputs to the correct formats before using the following functions as is.

In [53]:
# referenced from James Mullenbach, I had to change my inputs to the format required in order to just use the following functions. 

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.nn.init import xavier_uniform_
from torch.autograd import Variable
from math import floor


class BaseModel(nn.Module):

    def __init__(self, Y, embed_file):
        super(BaseModel, self).__init__()
        self.Y = Y  # label size

        # make embedding layer
        w = torch.Tensor(load_embeddings(embed_file))
        num_embeddings, embedding_dim = w.size()  
        # num_embeddings words in vocab, embedding_dim dimensional embeddings
        self.embed_size = embedding_dim

        self.embed = nn.Embedding(num_embeddings, embedding_dim, padding_idx=0)
        self.embed.weight.data = w.clone()
        # Make embedding weights non trainable
        self.embed.weight.requires_grad = True

class BOWPool(BaseModel):
    """
        Logistic regression model over average or max-pooled word vector input
    """

    def __init__(self, Y, embed_file):
        super(BOWPool, self).__init__(Y, embed_file)
        self.final = nn.Linear(self.embed_size, Y)
        xavier_uniform_(self.final.weight)
        self.embed_drop = nn.Dropout(p=0.5)

    def forward(self, x):
        seq_length = x.shape[1]
        x = self.embed(x)
        x = self.embed_drop(x)
        x = x.transpose(1, 2)
        x = nn.MaxPool1d(kernel_size=seq_length)(x)
        x = torch.squeeze(x, 2)
        x = self.final(x)
        return x

class VanillaCNN(BaseModel):
    def __init__(self, Y, embed_file):
        num_filters = 100
        kernel_size = 4
        super(VanillaCNN, self).__init__(Y, embed_file)
        self.conv = nn.Conv1d(self.embed_size, num_filters, kernel_size)
        xavier_uniform_(self.conv.weight)
        self.embed_drop = nn.Dropout(p=0.5)

        self.final = nn.Linear(num_filters, Y)
        xavier_uniform_(self.final.weight)

    def forward(self, x):
        x = self.embed(x)
        x = self.embed_drop(x)
        x = x.transpose(1, 2)
        x = self.conv(x)
        x = nn.MaxPool1d(x.size()[2])(torch.tanh(x))
        x = torch.squeeze(x, 2)
        # linear output
        x = self.final(x)
        return x

class BidirectionalGru(BaseModel):
    def __init__(self, Y, embed_file):
        super(BidirectionalGru, self).__init__(Y, embed_file)
        self.rnn_dim = 512
        self.num_directions = 2
        self.num_layers = 1
        self.rnn = nn.GRU(self.embed_size,
                          hidden_size=floor(self.rnn_dim / self.num_directions),
                          num_layers=self.num_layers,
                          bidirectional=True)
        self.final = nn.Linear(self.rnn_dim, Y)

    def forward(self, x):
        embeds = self.embed(x).transpose(0, 1)
        out, hidden = self.rnn(embeds)
        batch_size_current = hidden.shape[1]
        last_hidden = hidden[-2:].transpose(0, 1).contiguous().view(batch_size_current, -1)
        # print(last_hidden.size())
        yhat = self.final(last_hidden)
        return yhat

class CNNAttn(BaseModel):
    def __init__(self, Y, embed_file):
        num_filters = 50
        kernel_size = 10
        super(CNNAttn, self).__init__(Y, embed_file)
        self.conv = nn.Conv1d(self.embed_size, num_filters, kernel_size, padding=int(floor(kernel_size / 2)))
        xavier_uniform_(self.conv.weight)
        self.embed_drop = nn.Dropout(p=0.5)

        self.U = nn.Linear(num_filters, Y)
        xavier_uniform_(self.U.weight)

        self.final = nn.Linear(num_filters, Y)
        xavier_uniform_(self.final.weight)

    def forward(self, x):
        x = self.embed(x)
        x = self.embed_drop(x)
        x = x.transpose(1, 2)
        # apply convolution and nonlinearity (tanh)
        x = F.tanh(self.conv(x).transpose(1, 2))
        # apply attention
        alpha = F.softmax(self.U.weight.matmul(x.transpose(1, 2)), dim=2)
        # document representations are weighted sums using the attention. Can compute all at once as a matmul
        m = alpha.matmul(x)
        # final layer classification
        y = self.final.weight.mul(m).sum(dim=2).add(self.final.bias)

        return y

The following will initialize the BOW/LR model using the word2vec model and the index to code generated earlier.

In [54]:
model = BOWPool(len(ind2c), w2v_model.wv.vectors)

The following code segment contains a AverageMeter class which I found online. The following functions that comes after are used as it is referenced from (James Mullenbach, 2018) but modified to my liking. 

In [55]:
import numpy as np
import pandas as pd
from collections import defaultdict
import csv
import os
import time
import torch
from sklearn.metrics import accuracy_score, f1_score
from sklearn.metrics import roc_curve, auc

# Helper class that I found online, it's pretty good. Just computes the average. 
class AverageMeter(object):
    """Computes and stores the average and current value"""

    def __init__(self):
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/
def union_size(yhat, y, axis):
    # axis=0 for label-level union (macro). axis=1 for instance-level
    return np.logical_or(yhat, y).sum(axis=axis).astype(float)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/
def intersect_size(yhat, y, axis):
    # axis=0 for label-level union (macro). axis=1 for instance-level
    return np.logical_and(yhat, y).sum(axis=axis).astype(float)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def macro_accuracy(yhat, y):
    num = intersect_size(yhat, y, 0) / (union_size(yhat, y, 0) + 1e-10)
    return np.mean(num)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def macro_precision(yhat, y):
    num = intersect_size(yhat, y, 0) / (yhat.sum(axis=0) + 1e-10)
    return np.mean(num)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def macro_recall(yhat, y):
    num = intersect_size(yhat, y, 0) / (y.sum(axis=0) + 1e-10)
    return np.mean(num)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def macro_f1(yhat, y):
    prec = macro_precision(yhat, y)
    rec = macro_recall(yhat, y)
    if prec + rec == 0:
        f1 = 0.
    else:
        f1 = 2 * (prec * rec) / (prec + rec)
    return f1

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def micro_accuracy(yhatmic, ymic):
    return intersect_size(yhatmic, ymic, 0) / union_size(yhatmic, ymic, 0)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def micro_precision(yhatmic, ymic):
    return intersect_size(yhatmic, ymic, 0) / yhatmic.sum(axis=0)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def micro_recall(yhatmic, ymic):
    return intersect_size(yhatmic, ymic, 0) / ymic.sum(axis=0)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def micro_f1(yhatmic, ymic):
    prec = micro_precision(yhatmic, ymic)
    rec = micro_recall(yhatmic, ymic)
    if prec + rec == 0:
        f1 = 0.
    else:
        f1 = 2 * (prec * rec) / (prec + rec)
    return f1

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def inst_precision(yhat, y):
    num = intersect_size(yhat, y, 1) / yhat.sum(axis=1)
    # correct for divide-by-zeros
    num[np.isnan(num)] = 0.
    return np.mean(num)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def inst_recall(yhat, y):
    num = intersect_size(yhat, y, 1) / y.sum(axis=1)
    # correct for divide-by-zeros
    num[np.isnan(num)] = 0.
    return np.mean(num)

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def inst_f1(yhat, y):
    prec = inst_precision(yhat, y)
    rec = inst_recall(yhat, y)
    f1 = 2 * (prec * rec) / (prec + rec)
    return f1

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def precision_at_k(yhat_raw, y, k):
    # num true labels in top k predictions / k
    sortd = np.argsort(yhat_raw)[:, ::-1]
    topk = sortd[:, :k]

    # get precision at k for each example
    vals = []
    for i, tk in enumerate(topk):
        if len(tk) > 0:
            num_true_in_top_k = y[i, tk].sum()
            denom = len(tk)
            vals.append(num_true_in_top_k / float(denom))

    return np.mean(vals)


#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/evaluation.py
def auc_metrics(yhat_raw, y, ymic):
    if yhat_raw.shape[0] <= 1:
        return
    fpr = {}
    tpr = {}
    roc_auc = {}
    # get AUC for each label individually
    relevant_labels = []
    auc_labels = {}
    for i in range(y.shape[1]):
        # only if there are true positives for this label
        if y[:, i].sum() > 0:
            fpr[i], tpr[i], _ = roc_curve(y[:, i], yhat_raw[:, i])
            if len(fpr[i]) > 1 and len(tpr[i]) > 1:
                auc_score = auc(fpr[i], tpr[i])
                if not np.isnan(auc_score):
                    auc_labels["auc_%d" % i] = auc_score
                    relevant_labels.append(i)

    # macro-AUC: just average the auc scores
    aucs = []
    for i in relevant_labels:
        aucs.append(auc_labels['auc_%d' % i])
    roc_auc['auc_macro'] = np.mean(aucs)

    # micro-AUC: just look at each individual prediction
    yhatmic = yhat_raw.ravel()
    fpr["micro"], tpr["micro"], _ = roc_curve(ymic, yhatmic)
    roc_auc["auc_micro"] = auc(fpr["micro"], tpr["micro"])

    return roc_auc


#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/ modified to my liking
def train(model, device, data_loader, criterion, optimizer, epoch, print_freq=10, verbose=True):
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()

    y_hats = []
    y_all = []
    yhat_raws = []

    model.train()

    end = time.time()
    for i, (input, target) in enumerate(data_loader):
        # measure data loading time
        data_time.update(time.time() - end)

        if isinstance(input, tuple):
            input = tuple([e.to(device) if type(e) == torch.Tensor else e for e in input])
        else:
            input = input.to(device)
        target = target.to(device)

        optimizer.zero_grad()
        output = model(input)
        loss = criterion(output, target)
        assert not np.isnan(loss.item()), 'Model diverged with loss = NaN'

        loss.backward()
        optimizer.step()

        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()

        losses.update(loss.item(), target.size(0))
        y = target.cpu().detach().numpy()
        yhat = torch.sigmoid(output).cpu().detach().round().numpy()
        yhat_raw = torch.sigmoid(output).cpu().detach().numpy()
        y_all.append(y)
        y_hats.append(yhat)
        yhat_raws.append(yhat_raw)
        f1 = inst_f1(yhat, y)

        if i % print_freq == 0 and verbose:
            print('Epoch: [{0}][{1}/{2}]\t'
                  'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                  'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                  'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                  'F1 {f1:.3f} \t'.format(epoch,
                                          i,
                                          len(data_loader),
                                          batch_time=batch_time,
                                          data_time=data_time,
                                          loss=losses,
                                          f1=f1))

    y_hats = np.concatenate(y_hats, axis=0)
    y_all = np.concatenate(y_all, axis=0)
    yhat_raws = np.concatenate(yhat_raws, axis=0)

    mac_acc = macro_accuracy(y_hats, y_all)
    mac_rec = macro_recall(y_hats, y_all)
    mac_pre = macro_precision(y_hats, y_all)
    mic_acc = micro_accuracy(y_hats.ravel(), y_all.ravel())
    mic_rec = micro_recall(y_hats.ravel(), y_all.ravel())
    mic_pre = micro_precision(y_hats.ravel(), y_all.ravel())
    mic_f1 = micro_f1(y_hats.ravel(), y_all.ravel())
    mac_f1 = macro_f1(y_hats, y_all)
    auc_dict = auc_metrics(yhat_raws, y_all, y_all.ravel())

    print('Epoch: [{0}] \t'
          'Train: [{1}] \t'
          'Time {batch_time.avg:.3f}\t'
          'Data {data_time.avg:.3f}\t'
          'Loss {loss.avg:.4f} \t'
          'Macro Accuracy {mac_acc:.3f} \t'
          'Macro Recall {mac_rec:.3f} \t'
          'Macro Precision {mac_pre:.3f} \t'
          'Macro F1 {mac_f1:.3f} \t'
          'Macro AUC {mac_auc:.3f} \t'
          'Micro Accuracy {mic_acc:.3f} \t'
          'Micro Recall {mic_rec:.3f} \t'
          'Micro Precision {mic_pre:.3f} \t'
          'Micro F1 {mic_f1:.3f} \t'
          'Micro AUC {auc_micro:.3f} \t'.format(
        epoch,
        len(data_loader),
        batch_time=batch_time,
        data_time=data_time,
        loss=losses,
        mac_acc=mac_acc,
        mac_pre=mac_pre,
        mac_rec=mac_rec,
        mac_f1=mac_f1,
        mac_auc=auc_dict['auc_macro'],
        mic_acc=mic_acc,
        mic_pre=mic_pre,
        mic_rec=mic_rec,
        mic_f1=mic_f1,
        auc_micro=auc_dict['auc_micro']))

    return losses.avg, mac_acc, mac_pre, mac_rec, mac_f1, mic_acc, mic_pre, mic_rec, mic_f1, auc_dict['auc_macro']

#  referenced from James Mullenbach, https://github.com/jamesmullenbach/caml-mimic/ modified to my liking
def evaluate(model, device, data_loader, criterion, print_freq=10, verbose=True):
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()

    y_hats = []
    y_all = []
    yhat_raws = []

    model.eval()

    with torch.no_grad():
        end = time.time()
        for i, (input, target) in enumerate(data_loader):

            if isinstance(input, tuple):
                input = tuple([e.to(device) if type(e) == torch.Tensor else e for e in input])
            else:
                input = input.to(device)
            target = target.to(device)

            output = model(input)
            loss = criterion(output, target)

            # measure elapsed time
            batch_time.update(time.time() - end)
            end = time.time()

            losses.update(loss.item(), target.size(0))
            y = target.cpu().detach().numpy()
            y_all.append(y)
            yhat = torch.sigmoid(output).cpu().detach().round().numpy()
            y_hats.append(yhat)
            yhat_raw = torch.sigmoid(output).cpu().detach().numpy()
            yhat_raws.append(yhat_raw)

            if i % print_freq == 0 and verbose:
                print('Test: [{0}/{1}]\t'
                      'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                      'Loss {loss.val:.4f} ({loss.avg:.4f})\t'.format(i, len(data_loader),
                                                                      batch_time=batch_time,
                                                                      data_time=data_time,
                                                                      loss=losses,
                                                                      ))
    y_hats = np.concatenate(y_hats, axis=0)
    y_all = np.concatenate(y_all, axis=0)
    yhat_raws = np.concatenate(yhat_raws, axis=0)

    mac_acc = macro_accuracy(y_hats, y_all)
    mac_rec = macro_recall(y_hats, y_all)
    mac_pre = macro_precision(y_hats, y_all)
    mic_acc = micro_accuracy(y_hats.ravel(), y_all.ravel())
    mic_rec = micro_recall(y_hats.ravel(), y_all.ravel())
    mic_pre = micro_precision(y_hats.ravel(), y_all.ravel())
    mic_f1 = micro_f1(y_hats.ravel(), y_all.ravel())
    mac_f1 = macro_f1(y_hats, y_all)
    auc_dict = auc_metrics(yhat_raws, y_all, y_all.ravel())
    prec_at_5 = precision_at_k(yhat_raws, y_all, 5)
    prec_at_8 = precision_at_k(yhat_raws, y_all, 8)
    prec_at_15 = precision_at_k(yhat_raws, y_all, 15)

    print('Test: \t'
          'Loss {loss.avg:.4f} \t'
          'Macro Accuracy {mac_acc:.3f} \t'
          'Macro Recall {mac_rec:.3f} \t'
          'Macro Precision {mac_pre:.3f} \t'
          'Macro F1 {mac_f1:.3f} \t'
          'Macro AUC {mac_auc:.3f} \t'
          'Micro Accuracy {mic_acc:.3f} \t'
          'Micro Recall {mic_rec:.3f} \t'
          'Micro Precision {mic_pre:.3f} \t'
          'Micro F1 {mic_f1:.3f} \t'
          'Micro AUC {auc_micro:.3f} \t'
          'P@5 {prec_at_5:.3f} \t'
          'P@8 {prec_at_8:.3f} \t'
          'P@15 {prec_at_15:.3f} \t'.format(
        len(data_loader),
        data_time=data_time,
        loss=losses,
        mac_acc=mac_acc,
        mac_pre=mac_pre,
        mac_rec=mac_rec,
        mac_f1=mac_f1,
        mac_auc=auc_dict['auc_macro'],
        mic_acc=mic_acc,
        mic_pre=mic_pre,
        mic_rec=mic_rec,
        mic_f1=mic_f1,
        auc_micro=auc_dict['auc_micro'],
        prec_at_5=prec_at_5,
        prec_at_8=prec_at_8,
        prec_at_15=prec_at_15))

    return losses.avg, mac_acc, mac_pre, mac_rec, mac_f1, mic_acc, mic_pre, mic_rec, mic_f1, auc_dict[
        'auc_macro'], yhat_raws, y_all

Sets the device, criterio and optimizer.

In [56]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
torch.manual_seed(1)
if device == "cuda":
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

criterion = torch.nn.BCEWithLogitsLoss()
optimizer = torch.optim.Adam

An earlystopping class which I found online. It's pretty good. It is by Bjarte Mehus Sunde 2018

In [57]:
import numpy as np
import torch

# Reference: 2018 Bjarte Mehus Sunde
class EarlyStopping:
    """Early stops the training if validation loss doesn't improve after a given patience."""

    def __init__(self, patience=7, verbose=False, delta=0):
        """
        Args:
            patience (int): How long to wait after last time validation loss improved.
                            Default: 7
            verbose (bool): If True, prints a message for each validation loss improvement. 
                            Default: False
            delta (float): Minimum change in the monitored quantity to qualify as an improvement.
                            Default: 0
        """
        self.patience = patience
        self.verbose = verbose
        self.counter = 0
        self.best_score = None
        self.early_stop = False
        self.val_loss_min = np.Inf
        self.delta = delta

    def __call__(self, val_loss, model):

        score = -val_loss

        if self.best_score is None:
            self.best_score = score
            self.save_checkpoint(val_loss, model)
        elif score < self.best_score + self.delta:
            self.counter += 1
            print(f'EarlyStopping counter: {self.counter} out of {self.patience}')
            if self.counter >= self.patience:
                self.early_stop = True
        else:
            self.best_score = score
            self.save_checkpoint(val_loss, model)
            self.counter = 0

    def save_checkpoint(self, val_loss, model):
        '''Saves model when validation loss decrease.'''
        if self.verbose:
            print(f'Validation loss decreased ({self.val_loss_min:.6f} --> {val_loss:.6f}).  Saving model ...')
        torch.save(model.state_dict(), 'checkpoint.pt')
        self.val_loss_min = val_loss

## Model Training and Evaluation - CBOW-LR

The following code segment will train the model specified above which is the CBOW-LR model with early stopping and save the model accordingly.

In [58]:
early_stopping = EarlyStopping(patience=3, verbose=True)
optimizer = torch.optim.Adam(model.parameters())
model.to(device)
criterion.to(device)

train_losses, train_mac_accs, train_mac_recs, train_mac_pres, train_mac_f1s, train_mac_aucs = [], [], [], [], [], []
valid_losses, valid_mac_accs, valid_mac_recs, valid_mac_pres, valid_mac_f1s, valid_mac_aucs = [], [], [], [], [], []

for epoch in range(50):
    train_loss, train_mac_acc, train_mac_rec, train_mac_pre, train_mac_f1, \
    train_mic_acc, train_mic_rec, train_mic_pre, train_mic_f1, train_mac_auc = train(model, device, train_loader,
                                                                                     criterion, optimizer, epoch,
                                                                                     verbose=True)
    valid_loss, valid_mac_acc, valid_mac_rec, valid_mac_pre, valid_mac_f1, \
    valid_mic_acc, valid_mic_rec, valid_mic_pre, valid_mic_f1, valid_mac_auc, _, _ = evaluate(model, device,
                                                                                              valid_loader,
                                                                                              criterion,
                                                                                              verbose=True)

    train_losses.append(train_loss)
    valid_losses.append(valid_loss)

    train_mac_accs.append(train_mac_acc)
    valid_mac_accs.append(valid_mac_acc)

    train_mac_aucs.append(train_mac_auc)
    valid_mac_aucs.append(valid_mac_auc)

    # early_stopping needs the validation loss to check if it has decreased,
    # and if it has, it will make a checkpoint of the current model
    early_stopping(valid_loss, model)

    if early_stopping.early_stop:
        print("Early stopping")
        break

# Save the model. Best model is considered the latest (min loss)
torch.save(model, "model.best")

Epoch: [0][0/1486]	Time 1.984 (1.984)	Data 1.561 (1.561)	Loss 0.6945 (0.6945)	F1 0.005 	
Epoch: [0][10/1486]	Time 0.010 (0.191)	Data 0.006 (0.148)	Loss 0.4507 (0.5671)	F1 nan 	


<ipython-input-55-06c7b316185a>:118: RuntimeWarning: invalid value encountered in double_scalars
  f1 = 2 * (prec * rec) / (prec + rec)
<ipython-input-55-06c7b316185a>:100: RuntimeWarning: invalid value encountered in true_divide
  num = intersect_size(yhat, y, 1) / yhat.sum(axis=1)


Epoch: [0][20/1486]	Time 0.012 (0.106)	Data 0.008 (0.082)	Loss 0.2723 (0.4643)	F1 nan 	
Epoch: [0][30/1486]	Time 0.012 (0.075)	Data 0.007 (0.058)	Loss 0.1812 (0.3862)	F1 nan 	
Epoch: [0][40/1486]	Time 0.012 (0.060)	Data 0.008 (0.045)	Loss 0.1223 (0.3279)	F1 nan 	
Epoch: [0][50/1486]	Time 0.012 (0.051)	Data 0.008 (0.038)	Loss 0.0872 (0.2831)	F1 nan 	
Epoch: [0][60/1486]	Time 0.013 (0.044)	Data 0.008 (0.033)	Loss 0.0653 (0.2488)	F1 nan 	
Epoch: [0][70/1486]	Time 0.013 (0.040)	Data 0.008 (0.030)	Loss 0.0470 (0.2215)	F1 nan 	
Epoch: [0][80/1486]	Time 0.012 (0.036)	Data 0.008 (0.027)	Loss 0.0403 (0.1998)	F1 nan 	
Epoch: [0][90/1486]	Time 0.011 (0.034)	Data 0.007 (0.025)	Loss 0.0375 (0.1821)	F1 nan 	
Epoch: [0][100/1486]	Time 0.013 (0.031)	Data 0.009 (0.023)	Loss 0.0313 (0.1674)	F1 nan 	
Epoch: [0][110/1486]	Time 0.012 (0.030)	Data 0.008 (0.022)	Loss 0.0275 (0.1549)	F1 nan 	
Epoch: [0][120/1486]	Time 0.012 (0.028)	Data 0.008 (0.021)	Loss 0.0227 (0.1442)	F1 nan 	
Epoch: [0][130/1486]	Time 0.0

Epoch: [0][960/1486]	Time 0.013 (0.014)	Data 0.008 (0.009)	Loss 0.0089 (0.0276)	F1 nan 	
Epoch: [0][970/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0092 (0.0274)	F1 nan 	
Epoch: [0][980/1486]	Time 0.014 (0.014)	Data 0.010 (0.009)	Loss 0.0080 (0.0272)	F1 nan 	
Epoch: [0][990/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0097 (0.0270)	F1 nan 	
Epoch: [0][1000/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0111 (0.0269)	F1 nan 	
Epoch: [0][1010/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0099 (0.0267)	F1 nan 	
Epoch: [0][1020/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0093 (0.0265)	F1 nan 	
Epoch: [0][1030/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0108 (0.0263)	F1 nan 	
Epoch: [0][1040/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0099 (0.0262)	F1 nan 	
Epoch: [0][1050/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0094 (0.0260)	F1 nan 	
Epoch: [0][1060/1486]	Time 0.012 (0.014)	Data 0.008 (0.009)	Loss 0.0087 (0.0259)	F1 nan 	
Epoch: [0][107

Epoch: [1][80/1486]	Time 0.015 (0.037)	Data 0.011 (0.032)	Loss 0.0081 (0.0088)	F1 0.003 	
Epoch: [1][90/1486]	Time 0.015 (0.034)	Data 0.011 (0.030)	Loss 0.0088 (0.0088)	F1 nan 	
Epoch: [1][100/1486]	Time 0.014 (0.032)	Data 0.010 (0.028)	Loss 0.0103 (0.0088)	F1 nan 	
Epoch: [1][110/1486]	Time 0.014 (0.031)	Data 0.010 (0.026)	Loss 0.0086 (0.0088)	F1 nan 	
Epoch: [1][120/1486]	Time 0.014 (0.029)	Data 0.010 (0.025)	Loss 0.0085 (0.0089)	F1 nan 	
Epoch: [1][130/1486]	Time 0.014 (0.028)	Data 0.010 (0.024)	Loss 0.0096 (0.0089)	F1 nan 	
Epoch: [1][140/1486]	Time 0.014 (0.027)	Data 0.010 (0.023)	Loss 0.0086 (0.0089)	F1 nan 	
Epoch: [1][150/1486]	Time 0.014 (0.026)	Data 0.010 (0.022)	Loss 0.0078 (0.0089)	F1 nan 	
Epoch: [1][160/1486]	Time 0.015 (0.026)	Data 0.011 (0.021)	Loss 0.0089 (0.0089)	F1 nan 	
Epoch: [1][170/1486]	Time 0.015 (0.025)	Data 0.010 (0.021)	Loss 0.0094 (0.0089)	F1 nan 	
Epoch: [1][180/1486]	Time 0.015 (0.025)	Data 0.011 (0.020)	Loss 0.0097 (0.0089)	F1 nan 	
Epoch: [1][190/1486]	

...

Epoch: [28] 	Train: [1486] 	Time 0.014	Data 0.010	Loss 0.0064 	Macro Accuracy 0.007 	Macro Recall 0.008 	Macro Precision 0.045 	Macro F1 0.014 	Macro AUC 0.958 	Micro Accuracy 0.136 	Micro Recall 0.146 	Micro Precision 0.654 	Micro F1 0.239 	Micro AUC 0.986 	
Test: [0/372]	Time 2.264 (2.264)	Loss 0.0113 (0.0113)	
Test: [10/372]	Time 0.007 (0.213)	Loss 0.0120 (0.0119)	
Test: [20/372]	Time 0.008 (0.116)	Loss 0.0123 (0.0120)	
Test: [30/372]	Time 0.008 (0.081)	Loss 0.0121 (0.0120)	
Test: [40/372]	Time 0.008 (0.063)	Loss 0.0117 (0.0120)	
Test: [50/372]	Time 0.008 (0.053)	Loss 0.0126 (0.0120)	
Test: [60/372]	Time 0.008 (0.045)	Loss 0.0113 (0.0120)	
Test: [70/372]	Time 0.009 (0.040)	Loss 0.0125 (0.0121)	
Test: [80/372]	Time 0.009 (0.036)	Loss 0.0113 (0.0120)	
Test: [90/372]	Time 0.009 (0.033)	Loss 0.0125 (0.0120)	
Test: [100/372]	Time 0.008 (0.031)	Loss 0.0119 (0.0120)	
Test: [110/372]	Time 0.008 (0.029)	Loss 0.0118 (0.0120)	
Test: [120/372]	Time 0.009 (0.027)	Loss 0.0118 (0.0121)	
Test: [130

Epoch: [29][600/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0063 (0.0064)	F1 0.279 	
Epoch: [29][610/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0063 (0.0064)	F1 0.240 	
Epoch: [29][620/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0058 (0.0064)	F1 0.196 	
Epoch: [29][630/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0064 (0.0064)	F1 0.231 	
Epoch: [29][640/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0054 (0.0064)	F1 0.299 	
Epoch: [29][650/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0070 (0.0064)	F1 0.165 	
Epoch: [29][660/1486]	Time 0.012 (0.017)	Data 0.008 (0.013)	Loss 0.0058 (0.0064)	F1 0.248 	
Epoch: [29][670/1486]	Time 0.012 (0.017)	Data 0.008 (0.012)	Loss 0.0057 (0.0064)	F1 0.246 	
Epoch: [29][680/1486]	Time 0.012 (0.017)	Data 0.008 (0.012)	Loss 0.0070 (0.0064)	F1 0.257 	
Epoch: [29][690/1486]	Time 0.012 (0.017)	Data 0.008 (0.012)	Loss 0.0069 (0.0064)	F1 0.210 	
Epoch: [29][700/1486]	Time 0.012 (0.017)	Data 0.008 (0.012)	Loss 0.0063 (0.0064)

Epoch: [29] 	Train: [1486] 	Time 0.014	Data 0.010	Loss 0.0064 	Macro Accuracy 0.008 	Macro Recall 0.009 	Macro Precision 0.049 	Macro F1 0.015 	Macro AUC 0.959 	Micro Accuracy 0.137 	Micro Recall 0.148 	Micro Precision 0.655 	Micro F1 0.241 	Micro AUC 0.986 	
Test: [0/372]	Time 2.358 (2.358)	Loss 0.0114 (0.0114)	
Test: [10/372]	Time 0.006 (0.222)	Loss 0.0120 (0.0120)	
Test: [20/372]	Time 0.008 (0.120)	Loss 0.0124 (0.0121)	
Test: [30/372]	Time 0.008 (0.084)	Loss 0.0122 (0.0121)	
Test: [40/372]	Time 0.008 (0.066)	Loss 0.0119 (0.0121)	
Test: [50/372]	Time 0.009 (0.054)	Loss 0.0127 (0.0121)	
Test: [60/372]	Time 0.008 (0.047)	Loss 0.0114 (0.0121)	
Test: [70/372]	Time 0.008 (0.041)	Loss 0.0126 (0.0122)	
Test: [80/372]	Time 0.008 (0.037)	Loss 0.0114 (0.0121)	
Test: [90/372]	Time 0.009 (0.034)	Loss 0.0127 (0.0121)	
Test: [100/372]	Time 0.008 (0.032)	Loss 0.0120 (0.0122)	
Test: [110/372]	Time 0.009 (0.030)	Loss 0.0119 (0.0122)	
Test: [120/372]	Time 0.008 (0.028)	Loss 0.0120 (0.0122)	
Test: [130

Epoch: [30][600/1486]	Time 0.014 (0.019)	Data 0.010 (0.014)	Loss 0.0070 (0.0064)	F1 0.318 	
Epoch: [30][610/1486]	Time 0.013 (0.019)	Data 0.009 (0.014)	Loss 0.0057 (0.0064)	F1 0.219 	
Epoch: [30][620/1486]	Time 0.014 (0.019)	Data 0.009 (0.014)	Loss 0.0055 (0.0064)	F1 0.253 	
Epoch: [30][630/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0059 (0.0063)	F1 0.252 	
Epoch: [30][640/1486]	Time 0.013 (0.018)	Data 0.009 (0.014)	Loss 0.0071 (0.0064)	F1 0.270 	
Epoch: [30][650/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0068 (0.0064)	F1 0.204 	
Epoch: [30][660/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0062 (0.0064)	F1 0.341 	
Epoch: [30][670/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0059 (0.0064)	F1 0.327 	
Epoch: [30][680/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0066 (0.0064)	F1 0.199 	
Epoch: [30][690/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0060 (0.0064)	F1 0.184 	
Epoch: [30][700/1486]	Time 0.014 (0.018)	Data 0.009 (0.014)	Loss 0.0065 (0.0064)

Epoch: [30] 	Train: [1486] 	Time 0.016	Data 0.011	Loss 0.0064 	Macro Accuracy 0.009 	Macro Recall 0.010 	Macro Precision 0.052 	Macro F1 0.017 	Macro AUC 0.960 	Micro Accuracy 0.138 	Micro Recall 0.149 	Micro Precision 0.655 	Micro F1 0.243 	Micro AUC 0.986 	
Test: [0/372]	Time 1.881 (1.881)	Loss 0.0113 (0.0113)	
Test: [10/372]	Time 0.007 (0.178)	Loss 0.0119 (0.0119)	
Test: [20/372]	Time 0.008 (0.098)	Loss 0.0123 (0.0120)	
Test: [30/372]	Time 0.008 (0.069)	Loss 0.0121 (0.0120)	
Test: [40/372]	Time 0.008 (0.054)	Loss 0.0117 (0.0120)	
Test: [50/372]	Time 0.008 (0.045)	Loss 0.0126 (0.0120)	
Test: [60/372]	Time 0.008 (0.039)	Loss 0.0113 (0.0120)	
Test: [70/372]	Time 0.009 (0.035)	Loss 0.0124 (0.0121)	
Test: [80/372]	Time 0.009 (0.032)	Loss 0.0113 (0.0120)	
Test: [90/372]	Time 0.008 (0.029)	Loss 0.0126 (0.0120)	
Test: [100/372]	Time 0.009 (0.027)	Loss 0.0119 (0.0120)	
Test: [110/372]	Time 0.009 (0.025)	Loss 0.0117 (0.0121)	
Test: [120/372]	Time 0.009 (0.024)	Loss 0.0118 (0.0121)	
Test: [130

We save the file again giving it a more meaningful name.

In [59]:
torch.save(model, "lr_model_50_epoch.best")

## Model Traing and Evaluation - CAML

We initialize, train, evaluate and save the model.

In [58]:
model = CNNAttn(len(ind2c), w2v_model.wv.vectors)

In [59]:
early_stopping = EarlyStopping(patience=3, verbose=True)
optimizer = torch.optim.Adam(model.parameters())
model.to(device)
criterion.to(device)

train_losses, train_mac_accs, train_mac_recs, train_mac_pres, train_mac_f1s, train_mac_aucs = [], [], [], [], [], []
valid_losses, valid_mac_accs, valid_mac_recs, valid_mac_pres, valid_mac_f1s, valid_mac_aucs = [], [], [], [], [], []

for epoch in range(50):
    train_loss, train_mac_acc, train_mac_rec, train_mac_pre, train_mac_f1, \
    train_mic_acc, train_mic_rec, train_mic_pre, train_mic_f1, train_mac_auc = train(model, device, train_loader,
                                                                                     criterion, optimizer, epoch,
                                                                                     verbose=True)
    valid_loss, valid_mac_acc, valid_mac_rec, valid_mac_pre, valid_mac_f1, \
    valid_mic_acc, valid_mic_rec, valid_mic_pre, valid_mic_f1, valid_mac_auc, _, _ = evaluate(model, device,
                                                                                              valid_loader,
                                                                                              criterion,
                                                                                              verbose=True)

    train_losses.append(train_loss)
    valid_losses.append(valid_loss)

    train_mac_accs.append(train_mac_acc)
    valid_mac_accs.append(valid_mac_acc)

    train_mac_aucs.append(train_mac_auc)
    valid_mac_aucs.append(valid_mac_auc)

    # early_stopping needs the validation loss to check if it has decreased,
    # and if it has, it will make a checkpoint of the current model
    early_stopping(valid_loss, model)

    if early_stopping.early_stop:
        print("Early stopping")
        break

# Save the model. Best model is considered the latest (min loss)
torch.save(model, "cnnattn_model.best")

/home/yaolong/anaconda3/lib/python3.8/site-packages/torch/nn/functional.py:1698: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")
<ipython-input-55-06c7b316185a>:118: RuntimeWarning: invalid value encountered in double_scalars
  f1 = 2 * (prec * rec) / (prec + rec)


Epoch: [0][0/47536]	Time 2.424 (2.424)	Data 1.993 (1.993)	Loss 0.6940 (0.6940)	F1 0.003 	
Epoch: [0][10/47536]	Time 0.006 (0.228)	Data 0.004 (0.185)	Loss 0.6730 (0.6866)	F1 0.004 	
Epoch: [0][20/47536]	Time 0.008 (0.124)	Data 0.003 (0.099)	Loss 0.6109 (0.6654)	F1 nan 	


<ipython-input-55-06c7b316185a>:100: RuntimeWarning: invalid value encountered in true_divide
  num = intersect_size(yhat, y, 1) / yhat.sum(axis=1)


Epoch: [0][30/47536]	Time 0.009 (0.087)	Data 0.004 (0.069)	Loss 0.4201 (0.6135)	F1 nan 	
Epoch: [0][40/47536]	Time 0.008 (0.067)	Data 0.003 (0.053)	Loss 0.2005 (0.5363)	F1 nan 	
Epoch: [0][50/47536]	Time 0.008 (0.056)	Data 0.004 (0.043)	Loss 0.0881 (0.4585)	F1 nan 	
Epoch: [0][60/47536]	Time 0.008 (0.048)	Data 0.004 (0.037)	Loss 0.0506 (0.3949)	F1 nan 	
Epoch: [0][70/47536]	Time 0.007 (0.043)	Data 0.004 (0.032)	Loss 0.0432 (0.3455)	F1 nan 	
Epoch: [0][80/47536]	Time 0.009 (0.038)	Data 0.004 (0.029)	Loss 0.0296 (0.3070)	F1 nan 	
Epoch: [0][90/47536]	Time 0.009 (0.035)	Data 0.004 (0.026)	Loss 0.0267 (0.2765)	F1 nan 	
Epoch: [0][100/47536]	Time 0.010 (0.032)	Data 0.004 (0.024)	Loss 0.0267 (0.2516)	F1 nan 	
Epoch: [0][110/47536]	Time 0.008 (0.030)	Data 0.004 (0.022)	Loss 0.0276 (0.2310)	F1 nan 	
Epoch: [0][120/47536]	Time 0.008 (0.028)	Data 0.004 (0.021)	Loss 0.0198 (0.2137)	F1 nan 	
Epoch: [0][130/47536]	Time 0.008 (0.027)	Data 0.004 (0.019)	Loss 0.0229 (0.1989)	F1 nan 	
Epoch: [0][140/47

Epoch: [0][960/47536]	Time 0.010 (0.011)	Data 0.005 (0.006)	Loss 0.0091 (0.0364)	F1 nan 	
Epoch: [0][970/47536]	Time 0.009 (0.011)	Data 0.004 (0.006)	Loss 0.0062 (0.0361)	F1 nan 	
Epoch: [0][980/47536]	Time 0.008 (0.011)	Data 0.004 (0.006)	Loss 0.0052 (0.0359)	F1 nan 	
Epoch: [0][990/47536]	Time 0.009 (0.011)	Data 0.004 (0.006)	Loss 0.0091 (0.0356)	F1 nan 	
Epoch: [0][1000/47536]	Time 0.008 (0.011)	Data 0.004 (0.006)	Loss 0.0093 (0.0353)	F1 nan 	
Epoch: [0][1010/47536]	Time 0.006 (0.011)	Data 0.004 (0.006)	Loss 0.0083 (0.0351)	F1 nan 	
Epoch: [0][1020/47536]	Time 0.008 (0.011)	Data 0.004 (0.006)	Loss 0.0056 (0.0348)	F1 nan 	
Epoch: [0][1030/47536]	Time 0.008 (0.011)	Data 0.004 (0.006)	Loss 0.0037 (0.0346)	F1 nan 	
Epoch: [0][1040/47536]	Time 0.006 (0.011)	Data 0.004 (0.006)	Loss 0.0065 (0.0343)	F1 nan 	
Epoch: [0][1050/47536]	Time 0.008 (0.011)	Data 0.004 (0.006)	Loss 0.0037 (0.0341)	F1 nan 	
Epoch: [0][1060/47536]	Time 0.010 (0.011)	Data 0.005 (0.006)	Loss 0.0106 (0.0338)	F1 nan 	
Epo

...

Test: [6100/11885]	Time 0.003 (0.003)	Loss 0.0096 (0.0064)	
Test: [6110/11885]	Time 0.002 (0.003)	Loss 0.0037 (0.0064)	
Test: [6120/11885]	Time 0.002 (0.003)	Loss 0.0097 (0.0064)	
Test: [6130/11885]	Time 0.003 (0.003)	Loss 0.0076 (0.0064)	
Test: [6140/11885]	Time 0.002 (0.003)	Loss 0.0036 (0.0064)	
Test: [6150/11885]	Time 0.003 (0.003)	Loss 0.0016 (0.0064)	
Test: [6160/11885]	Time 0.001 (0.003)	Loss 0.0088 (0.0064)	
Test: [6170/11885]	Time 0.002 (0.003)	Loss 0.0047 (0.0064)	
Test: [6180/11885]	Time 0.003 (0.003)	Loss 0.0036 (0.0064)	
Test: [6190/11885]	Time 0.002 (0.003)	Loss 0.0106 (0.0064)	
Test: [6200/11885]	Time 0.002 (0.003)	Loss 0.0024 (0.0063)	
Test: [6210/11885]	Time 0.002 (0.003)	Loss 0.0058 (0.0063)	
Test: [6220/11885]	Time 0.003 (0.003)	Loss 0.0030 (0.0063)	
Test: [6230/11885]	Time 0.002 (0.003)	Loss 0.0074 (0.0063)	
Test: [6240/11885]	Time 0.002 (0.003)	Loss 0.0066 (0.0063)	
Test: [6250/11885]	Time 0.003 (0.003)	Loss 0.0028 (0.0063)	
Test: [6260/11885]	Time 0.003 (0.003)	Lo

Test: [7540/11885]	Time 0.002 (0.003)	Loss 0.0077 (0.0064)	
Test: [7550/11885]	Time 0.003 (0.003)	Loss 0.0054 (0.0064)	
Test: [7560/11885]	Time 0.002 (0.003)	Loss 0.0027 (0.0064)	
Test: [7570/11885]	Time 0.002 (0.003)	Loss 0.0050 (0.0064)	
Test: [7580/11885]	Time 0.001 (0.003)	Loss 0.0029 (0.0064)	
Test: [7590/11885]	Time 0.002 (0.003)	Loss 0.0031 (0.0064)	
Test: [7600/11885]	Time 0.003 (0.003)	Loss 0.0031 (0.0064)	
Test: [7610/11885]	Time 0.002 (0.003)	Loss 0.0041 (0.0063)	
Test: [7620/11885]	Time 0.002 (0.003)	Loss 0.0064 (0.0063)	
Test: [7630/11885]	Time 0.002 (0.003)	Loss 0.0057 (0.0064)	
Test: [7640/11885]	Time 0.002 (0.003)	Loss 0.0067 (0.0063)	
Test: [7650/11885]	Time 0.002 (0.003)	Loss 0.0046 (0.0063)	
Test: [7660/11885]	Time 0.003 (0.003)	Loss 0.0020 (0.0063)	
Test: [7670/11885]	Time 0.002 (0.003)	Loss 0.0071 (0.0063)	
Test: [7680/11885]	Time 0.001 (0.003)	Loss 0.0199 (0.0063)	
Test: [7690/11885]	Time 0.002 (0.003)	Loss 0.0079 (0.0063)	
Test: [7700/11885]	Time 0.003 (0.003)	Lo

Test: [8910/11885]	Time 0.002 (0.003)	Loss 0.0019 (0.0063)	
Test: [8920/11885]	Time 0.005 (0.003)	Loss 0.0063 (0.0063)	
Test: [8930/11885]	Time 0.003 (0.003)	Loss 0.0017 (0.0063)	
Test: [8940/11885]	Time 0.002 (0.003)	Loss 0.0028 (0.0063)	
Test: [8950/11885]	Time 0.002 (0.003)	Loss 0.0041 (0.0063)	
Test: [8960/11885]	Time 0.002 (0.003)	Loss 0.0100 (0.0063)	
Test: [8970/11885]	Time 0.002 (0.003)	Loss 0.0091 (0.0063)	
Test: [8980/11885]	Time 0.002 (0.003)	Loss 0.0033 (0.0063)	
Test: [8990/11885]	Time 0.003 (0.003)	Loss 0.0040 (0.0063)	
Test: [9000/11885]	Time 0.002 (0.003)	Loss 0.0041 (0.0063)	
Test: [9010/11885]	Time 0.002 (0.003)	Loss 0.0062 (0.0063)	
Test: [9020/11885]	Time 0.002 (0.003)	Loss 0.0146 (0.0063)	
Test: [9030/11885]	Time 0.002 (0.003)	Loss 0.0020 (0.0063)	
Test: [9040/11885]	Time 0.002 (0.003)	Loss 0.0050 (0.0063)	
Test: [9050/11885]	Time 0.003 (0.003)	Loss 0.0031 (0.0063)	
Test: [9060/11885]	Time 0.002 (0.003)	Loss 0.0028 (0.0063)	
Test: [9070/11885]	Time 0.002 (0.003)	Lo

Test: [10350/11885]	Time 0.004 (0.003)	Loss 0.0154 (0.0063)	
Test: [10360/11885]	Time 0.003 (0.003)	Loss 0.0048 (0.0063)	
Test: [10370/11885]	Time 0.002 (0.003)	Loss 0.0111 (0.0063)	
Test: [10380/11885]	Time 0.003 (0.003)	Loss 0.0022 (0.0063)	
Test: [10390/11885]	Time 0.002 (0.003)	Loss 0.0063 (0.0063)	
Test: [10400/11885]	Time 0.002 (0.003)	Loss 0.0052 (0.0063)	
Test: [10410/11885]	Time 0.003 (0.003)	Loss 0.0051 (0.0063)	
Test: [10420/11885]	Time 0.003 (0.003)	Loss 0.0025 (0.0063)	
Test: [10430/11885]	Time 0.002 (0.003)	Loss 0.0064 (0.0063)	
Test: [10440/11885]	Time 0.003 (0.003)	Loss 0.0046 (0.0063)	
Test: [10450/11885]	Time 0.002 (0.003)	Loss 0.0033 (0.0063)	
Test: [10460/11885]	Time 0.003 (0.003)	Loss 0.0063 (0.0063)	
Test: [10470/11885]	Time 0.003 (0.003)	Loss 0.0101 (0.0063)	
Test: [10480/11885]	Time 0.002 (0.003)	Loss 0.0013 (0.0063)	
Test: [10490/11885]	Time 0.002 (0.003)	Loss 0.0100 (0.0063)	
Test: [10500/11885]	Time 0.002 (0.003)	Loss 0.0050 (0.0063)	
Test: [10510/11885]	Time

Test: [11740/11885]	Time 0.002 (0.003)	Loss 0.0025 (0.0063)	
Test: [11750/11885]	Time 0.002 (0.003)	Loss 0.0070 (0.0063)	
Test: [11760/11885]	Time 0.002 (0.003)	Loss 0.0063 (0.0063)	
Test: [11770/11885]	Time 0.003 (0.003)	Loss 0.0097 (0.0063)	
Test: [11780/11885]	Time 0.001 (0.003)	Loss 0.0094 (0.0063)	
Test: [11790/11885]	Time 0.002 (0.003)	Loss 0.0025 (0.0063)	
Test: [11800/11885]	Time 0.003 (0.003)	Loss 0.0082 (0.0063)	
Test: [11810/11885]	Time 0.003 (0.003)	Loss 0.0034 (0.0063)	
Test: [11820/11885]	Time 0.002 (0.003)	Loss 0.0051 (0.0063)	
Test: [11830/11885]	Time 0.003 (0.003)	Loss 0.0085 (0.0063)	
Test: [11840/11885]	Time 0.003 (0.003)	Loss 0.0030 (0.0063)	
Test: [11850/11885]	Time 0.002 (0.003)	Loss 0.0027 (0.0063)	
Test: [11860/11885]	Time 0.002 (0.003)	Loss 0.0042 (0.0063)	
Test: [11870/11885]	Time 0.003 (0.003)	Loss 0.0027 (0.0063)	
Test: [11880/11885]	Time 0.001 (0.003)	Loss 0.0035 (0.0063)	
Test: 	Loss 0.0063 	Macro Accuracy 0.021 	Macro Recall 0.030 	Macro Precision 0.046 	

## Model Training and Evaluation - Bidirectional GRU

We initialize, train, evaluate and save the BiGRU model.

In [58]:
model = BidirectionalGru(len(ind2c), w2v_model.wv.vectors)

In [59]:
early_stopping = EarlyStopping(patience=3, verbose=True)
optimizer = torch.optim.Adam(model.parameters())
model.to(device)
criterion.to(device)

train_losses, train_mac_accs, train_mac_recs, train_mac_pres, train_mac_f1s, train_mac_aucs = [], [], [], [], [], []
valid_losses, valid_mac_accs, valid_mac_recs, valid_mac_pres, valid_mac_f1s, valid_mac_aucs = [], [], [], [], [], []

for epoch in range(50):
    train_loss, train_mac_acc, train_mac_rec, train_mac_pre, train_mac_f1, \
    train_mic_acc, train_mic_rec, train_mic_pre, train_mic_f1, train_mac_auc = train(model, device, train_loader,
                                                                                     criterion, optimizer, epoch,
                                                                                     verbose=True)
    valid_loss, valid_mac_acc, valid_mac_rec, valid_mac_pre, valid_mac_f1, \
    valid_mic_acc, valid_mic_rec, valid_mic_pre, valid_mic_f1, valid_mac_auc, _, _ = evaluate(model, device,
                                                                                              valid_loader,
                                                                                              criterion,
                                                                                              verbose=True)

    train_losses.append(train_loss)
    valid_losses.append(valid_loss)

    train_mac_accs.append(train_mac_acc)
    valid_mac_accs.append(valid_mac_acc)

    train_mac_aucs.append(train_mac_auc)
    valid_mac_aucs.append(valid_mac_auc)

    # early_stopping needs the validation loss to check if it has decreased,
    # and if it has, it will make a checkpoint of the current model
    early_stopping(valid_loss, model)

    if early_stopping.early_stop:
        print("Early stopping")
        break

# Save the model. Best model is considered the latest (min loss)
torch.save(model, "gru_model.best")

Epoch: [0][0/1486]	Time 1.698 (1.698)	Data 1.477 (1.477)	Loss 0.6933 (0.6933)	F1 0.004 	


<ipython-input-55-06c7b316185a>:118: RuntimeWarning: invalid value encountered in double_scalars
  f1 = 2 * (prec * rec) / (prec + rec)
<ipython-input-55-06c7b316185a>:100: RuntimeWarning: invalid value encountered in true_divide
  num = intersect_size(yhat, y, 1) / yhat.sum(axis=1)


Epoch: [0][10/1486]	Time 0.175 (0.320)	Data 0.010 (0.145)	Loss 0.0449 (0.4963)	F1 nan 	
Epoch: [0][20/1486]	Time 0.205 (0.255)	Data 0.009 (0.081)	Loss 0.0105 (0.2663)	F1 0.044 	
Epoch: [0][30/1486]	Time 0.183 (0.235)	Data 0.008 (0.058)	Loss 0.0113 (0.1841)	F1 nan 	
Epoch: [0][40/1486]	Time 0.171 (0.224)	Data 0.009 (0.046)	Loss 0.0105 (0.1418)	F1 0.030 	
Epoch: [0][50/1486]	Time 0.187 (0.215)	Data 0.009 (0.039)	Loss 0.0085 (0.1158)	F1 nan 	
Epoch: [0][60/1486]	Time 0.179 (0.212)	Data 0.010 (0.034)	Loss 0.0098 (0.0984)	F1 nan 	
Epoch: [0][70/1486]	Time 0.209 (0.211)	Data 0.011 (0.031)	Loss 0.0091 (0.0859)	F1 nan 	
Epoch: [0][80/1486]	Time 0.201 (0.210)	Data 0.012 (0.028)	Loss 0.0093 (0.0765)	F1 nan 	
Epoch: [0][90/1486]	Time 0.181 (0.208)	Data 0.011 (0.027)	Loss 0.0094 (0.0691)	F1 nan 	
Epoch: [0][100/1486]	Time 0.184 (0.206)	Data 0.012 (0.025)	Loss 0.0089 (0.0632)	F1 nan 	
Epoch: [0][110/1486]	Time 0.180 (0.204)	Data 0.011 (0.024)	Loss 0.0097 (0.0584)	F1 nan 	
Epoch: [0][120/1486]	Time 

Epoch: [0][940/1486]	Time 0.206 (0.192)	Data 0.010 (0.012)	Loss 0.0079 (0.0150)	F1 nan 	
Epoch: [0][950/1486]	Time 0.174 (0.192)	Data 0.010 (0.012)	Loss 0.0091 (0.0149)	F1 nan 	
Epoch: [0][960/1486]	Time 0.182 (0.192)	Data 0.010 (0.012)	Loss 0.0093 (0.0149)	F1 nan 	
Epoch: [0][970/1486]	Time 0.205 (0.192)	Data 0.009 (0.012)	Loss 0.0088 (0.0148)	F1 nan 	
Epoch: [0][980/1486]	Time 0.198 (0.192)	Data 0.012 (0.012)	Loss 0.0091 (0.0148)	F1 nan 	
Epoch: [0][990/1486]	Time 0.170 (0.192)	Data 0.008 (0.012)	Loss 0.0090 (0.0147)	F1 0.045 	
Epoch: [0][1000/1486]	Time 0.206 (0.192)	Data 0.011 (0.012)	Loss 0.0092 (0.0147)	F1 nan 	
Epoch: [0][1010/1486]	Time 0.172 (0.192)	Data 0.010 (0.012)	Loss 0.0088 (0.0146)	F1 nan 	
Epoch: [0][1020/1486]	Time 0.210 (0.192)	Data 0.012 (0.012)	Loss 0.0080 (0.0145)	F1 nan 	
Epoch: [0][1030/1486]	Time 0.203 (0.192)	Data 0.008 (0.012)	Loss 0.0089 (0.0145)	F1 nan 	
Epoch: [0][1040/1486]	Time 0.206 (0.192)	Data 0.011 (0.012)	Loss 0.0079 (0.0145)	F1 nan 	
Epoch: [0][105

<ipython-input-55-06c7b316185a>:79: RuntimeWarning: invalid value encountered in double_scalars
  return intersect_size(yhatmic, ymic, 0) / yhatmic.sum(axis=0)


...

Epoch: [10][1050/1486]	Time 0.182 (0.202)	Data 0.013 (0.015)	Loss 0.0049 (0.0048)	F1 0.472 	
Epoch: [10][1060/1486]	Time 0.188 (0.202)	Data 0.013 (0.015)	Loss 0.0043 (0.0048)	F1 0.450 	
Epoch: [10][1070/1486]	Time 0.219 (0.202)	Data 0.012 (0.015)	Loss 0.0048 (0.0048)	F1 0.463 	
Epoch: [10][1080/1486]	Time 0.179 (0.202)	Data 0.013 (0.015)	Loss 0.0046 (0.0048)	F1 0.432 	
Epoch: [10][1090/1486]	Time 0.180 (0.201)	Data 0.013 (0.015)	Loss 0.0044 (0.0048)	F1 0.469 	
Epoch: [10][1100/1486]	Time 0.252 (0.201)	Data 0.013 (0.015)	Loss 0.0045 (0.0048)	F1 0.429 	
Epoch: [10][1110/1486]	Time 0.183 (0.201)	Data 0.014 (0.015)	Loss 0.0051 (0.0048)	F1 0.449 	
Epoch: [10][1120/1486]	Time 0.218 (0.201)	Data 0.014 (0.015)	Loss 0.0046 (0.0048)	F1 0.465 	
Epoch: [10][1130/1486]	Time 0.187 (0.201)	Data 0.013 (0.015)	Loss 0.0047 (0.0048)	F1 0.472 	
Epoch: [10][1140/1486]	Time 0.206 (0.201)	Data 0.014 (0.015)	Loss 0.0046 (0.0048)	F1 0.474 	
Epoch: [10][1150/1486]	Time 0.186 (0.201)	Data 0.014 (0.015)	Loss 0.00

Epoch: [11][160/1486]	Time 0.210 (0.214)	Data 0.013 (0.026)	Loss 0.0045 (0.0044)	F1 0.520 	
Epoch: [11][170/1486]	Time 0.185 (0.213)	Data 0.013 (0.025)	Loss 0.0047 (0.0044)	F1 0.462 	
Epoch: [11][180/1486]	Time 0.176 (0.212)	Data 0.012 (0.025)	Loss 0.0040 (0.0044)	F1 0.519 	
Epoch: [11][190/1486]	Time 0.219 (0.212)	Data 0.012 (0.024)	Loss 0.0049 (0.0044)	F1 0.474 	
Epoch: [11][200/1486]	Time 0.230 (0.212)	Data 0.018 (0.023)	Loss 0.0048 (0.0044)	F1 0.463 	
Epoch: [11][210/1486]	Time 0.212 (0.211)	Data 0.015 (0.023)	Loss 0.0044 (0.0044)	F1 0.520 	
Epoch: [11][220/1486]	Time 0.232 (0.212)	Data 0.012 (0.022)	Loss 0.0052 (0.0044)	F1 0.497 	
Epoch: [11][230/1486]	Time 0.178 (0.211)	Data 0.014 (0.022)	Loss 0.0045 (0.0044)	F1 0.490 	
Epoch: [11][240/1486]	Time 0.205 (0.210)	Data 0.013 (0.022)	Loss 0.0039 (0.0044)	F1 0.486 	
Epoch: [11][250/1486]	Time 0.196 (0.210)	Data 0.013 (0.021)	Loss 0.0038 (0.0044)	F1 0.472 	
Epoch: [11][260/1486]	Time 0.186 (0.209)	Data 0.014 (0.021)	Loss 0.0036 (0.0044)

Epoch: [11][1050/1486]	Time 0.184 (0.203)	Data 0.013 (0.015)	Loss 0.0054 (0.0045)	F1 0.466 	
Epoch: [11][1060/1486]	Time 0.187 (0.203)	Data 0.017 (0.015)	Loss 0.0042 (0.0045)	F1 0.478 	
Epoch: [11][1070/1486]	Time 0.190 (0.203)	Data 0.016 (0.015)	Loss 0.0042 (0.0045)	F1 0.505 	
Epoch: [11][1080/1486]	Time 0.182 (0.203)	Data 0.012 (0.015)	Loss 0.0043 (0.0045)	F1 0.434 	
Epoch: [11][1090/1486]	Time 0.184 (0.203)	Data 0.012 (0.015)	Loss 0.0044 (0.0045)	F1 0.427 	
Epoch: [11][1100/1486]	Time 0.247 (0.203)	Data 0.013 (0.015)	Loss 0.0042 (0.0045)	F1 0.499 	
Epoch: [11][1110/1486]	Time 0.184 (0.203)	Data 0.012 (0.015)	Loss 0.0042 (0.0045)	F1 0.517 	
Epoch: [11][1120/1486]	Time 0.250 (0.203)	Data 0.014 (0.015)	Loss 0.0046 (0.0045)	F1 0.544 	
Epoch: [11][1130/1486]	Time 0.207 (0.203)	Data 0.013 (0.015)	Loss 0.0040 (0.0045)	F1 0.505 	
Epoch: [11][1140/1486]	Time 0.172 (0.203)	Data 0.012 (0.015)	Loss 0.0045 (0.0045)	F1 0.449 	
Epoch: [11][1150/1486]	Time 0.208 (0.203)	Data 0.013 (0.015)	Loss 0.00

Epoch: [12][160/1486]	Time 0.211 (0.213)	Data 0.014 (0.026)	Loss 0.0038 (0.0042)	F1 0.537 	
Epoch: [12][170/1486]	Time 0.188 (0.212)	Data 0.011 (0.025)	Loss 0.0036 (0.0042)	F1 0.530 	
Epoch: [12][180/1486]	Time 0.179 (0.210)	Data 0.013 (0.024)	Loss 0.0040 (0.0042)	F1 0.464 	
Epoch: [12][190/1486]	Time 0.203 (0.210)	Data 0.013 (0.024)	Loss 0.0039 (0.0042)	F1 0.558 	
Epoch: [12][200/1486]	Time 0.237 (0.210)	Data 0.011 (0.023)	Loss 0.0045 (0.0042)	F1 0.540 	
Epoch: [12][210/1486]	Time 0.246 (0.209)	Data 0.013 (0.023)	Loss 0.0043 (0.0042)	F1 0.515 	
Epoch: [12][220/1486]	Time 0.182 (0.208)	Data 0.013 (0.022)	Loss 0.0042 (0.0042)	F1 0.525 	
Epoch: [12][230/1486]	Time 0.251 (0.208)	Data 0.013 (0.022)	Loss 0.0040 (0.0042)	F1 0.467 	
Epoch: [12][240/1486]	Time 0.184 (0.207)	Data 0.014 (0.022)	Loss 0.0040 (0.0042)	F1 0.517 	
Epoch: [12][250/1486]	Time 0.181 (0.208)	Data 0.013 (0.021)	Loss 0.0050 (0.0042)	F1 0.505 	
Epoch: [12][260/1486]	Time 0.205 (0.207)	Data 0.013 (0.021)	Loss 0.0040 (0.0042)

Epoch: [12][1050/1486]	Time 0.216 (0.201)	Data 0.014 (0.015)	Loss 0.0041 (0.0043)	F1 0.490 	
Epoch: [12][1060/1486]	Time 0.183 (0.201)	Data 0.011 (0.015)	Loss 0.0050 (0.0043)	F1 0.498 	
Epoch: [12][1070/1486]	Time 0.208 (0.201)	Data 0.013 (0.015)	Loss 0.0045 (0.0043)	F1 0.477 	
Epoch: [12][1080/1486]	Time 0.182 (0.201)	Data 0.012 (0.015)	Loss 0.0048 (0.0043)	F1 0.459 	
Epoch: [12][1090/1486]	Time 0.186 (0.201)	Data 0.013 (0.015)	Loss 0.0044 (0.0043)	F1 0.533 	
Epoch: [12][1100/1486]	Time 0.192 (0.201)	Data 0.014 (0.015)	Loss 0.0039 (0.0043)	F1 0.564 	
Epoch: [12][1110/1486]	Time 0.228 (0.201)	Data 0.011 (0.015)	Loss 0.0049 (0.0043)	F1 0.502 	
Epoch: [12][1120/1486]	Time 0.185 (0.201)	Data 0.013 (0.015)	Loss 0.0040 (0.0043)	F1 0.510 	
Epoch: [12][1130/1486]	Time 0.176 (0.201)	Data 0.011 (0.015)	Loss 0.0046 (0.0043)	F1 0.497 	
Epoch: [12][1140/1486]	Time 0.179 (0.201)	Data 0.011 (0.015)	Loss 0.0048 (0.0043)	F1 0.508 	
Epoch: [12][1150/1486]	Time 0.182 (0.201)	Data 0.011 (0.015)	Loss 0.00

## Model Training and Evaluation - CNN

We initialize, train, evaluate and save the CNN Model.

In [58]:
model = VanillaCNN(len(ind2c), w2v_model.wv.vectors)

In [59]:
early_stopping = EarlyStopping(patience=3, verbose=True)
optimizer = torch.optim.Adam(model.parameters())
model.to(device)
criterion.to(device)

train_losses, train_mac_accs, train_mac_recs, train_mac_pres, train_mac_f1s, train_mac_aucs = [], [], [], [], [], []
valid_losses, valid_mac_accs, valid_mac_recs, valid_mac_pres, valid_mac_f1s, valid_mac_aucs = [], [], [], [], [], []

for epoch in range(50):
    train_loss, train_mac_acc, train_mac_rec, train_mac_pre, train_mac_f1, \
    train_mic_acc, train_mic_rec, train_mic_pre, train_mic_f1, train_mac_auc = train(model, device, train_loader,
                                                                                     criterion, optimizer, epoch,
                                                                                     verbose=True)
    valid_loss, valid_mac_acc, valid_mac_rec, valid_mac_pre, valid_mac_f1, \
    valid_mic_acc, valid_mic_rec, valid_mic_pre, valid_mic_f1, valid_mac_auc, _, _ = evaluate(model, device,
                                                                                              valid_loader,
                                                                                              criterion,
                                                                                              verbose=True)

    train_losses.append(train_loss)
    valid_losses.append(valid_loss)

    train_mac_accs.append(train_mac_acc)
    valid_mac_accs.append(valid_mac_acc)

    train_mac_aucs.append(train_mac_auc)
    valid_mac_aucs.append(valid_mac_auc)

    # early_stopping needs the validation loss to check if it has decreased,
    # and if it has, it will make a checkpoint of the current model
    early_stopping(valid_loss, model)

    if early_stopping.early_stop:
        print("Early stopping")
        break

# Save the model. Best model is considered the latest (min loss)
torch.save(model, "cnn_model.best")

Epoch: [0][0/1486]	Time 2.362 (2.362)	Data 1.913 (1.913)	Loss 0.6941 (0.6941)	F1 0.003 	
Epoch: [0][10/1486]	Time 0.017 (0.232)	Data 0.007 (0.182)	Loss 0.4747 (0.5850)	F1 nan 	


<ipython-input-55-06c7b316185a>:118: RuntimeWarning: invalid value encountered in double_scalars
  f1 = 2 * (prec * rec) / (prec + rec)
<ipython-input-55-06c7b316185a>:100: RuntimeWarning: invalid value encountered in true_divide
  num = intersect_size(yhat, y, 1) / yhat.sum(axis=1)


Epoch: [0][20/1486]	Time 0.018 (0.131)	Data 0.008 (0.100)	Loss 0.2597 (0.4743)	F1 nan 	
Epoch: [0][30/1486]	Time 0.018 (0.094)	Data 0.009 (0.070)	Loss 0.1249 (0.3789)	F1 nan 	
Epoch: [0][40/1486]	Time 0.019 (0.076)	Data 0.009 (0.056)	Loss 0.0577 (0.3067)	F1 nan 	
Epoch: [0][50/1486]	Time 0.021 (0.065)	Data 0.011 (0.047)	Loss 0.0373 (0.2554)	F1 nan 	
Epoch: [0][60/1486]	Time 0.019 (0.058)	Data 0.010 (0.041)	Loss 0.0278 (0.2188)	F1 nan 	
Epoch: [0][70/1486]	Time 0.019 (0.053)	Data 0.010 (0.037)	Loss 0.0226 (0.1914)	F1 nan 	
Epoch: [0][80/1486]	Time 0.018 (0.048)	Data 0.009 (0.033)	Loss 0.0205 (0.1704)	F1 nan 	
Epoch: [0][90/1486]	Time 0.019 (0.045)	Data 0.009 (0.031)	Loss 0.0184 (0.1538)	F1 nan 	
Epoch: [0][100/1486]	Time 0.019 (0.043)	Data 0.009 (0.028)	Loss 0.0174 (0.1403)	F1 nan 	
Epoch: [0][110/1486]	Time 0.019 (0.041)	Data 0.009 (0.027)	Loss 0.0168 (0.1292)	F1 nan 	
Epoch: [0][120/1486]	Time 0.019 (0.039)	Data 0.009 (0.025)	Loss 0.0170 (0.1199)	F1 nan 	
Epoch: [0][130/1486]	Time 0.0

Epoch: [0][960/1486]	Time 0.019 (0.022)	Data 0.010 (0.012)	Loss 0.0099 (0.0238)	F1 nan 	
Epoch: [0][970/1486]	Time 0.019 (0.022)	Data 0.010 (0.012)	Loss 0.0098 (0.0237)	F1 nan 	
Epoch: [0][980/1486]	Time 0.020 (0.022)	Data 0.010 (0.012)	Loss 0.0080 (0.0235)	F1 nan 	
Epoch: [0][990/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.0091 (0.0234)	F1 nan 	
Epoch: [0][1000/1486]	Time 0.025 (0.022)	Data 0.015 (0.012)	Loss 0.0091 (0.0232)	F1 nan 	
Epoch: [0][1010/1486]	Time 0.019 (0.022)	Data 0.009 (0.011)	Loss 0.0082 (0.0231)	F1 nan 	
Epoch: [0][1020/1486]	Time 0.019 (0.022)	Data 0.009 (0.011)	Loss 0.0082 (0.0229)	F1 nan 	
Epoch: [0][1030/1486]	Time 0.019 (0.022)	Data 0.009 (0.011)	Loss 0.0088 (0.0228)	F1 nan 	
Epoch: [0][1040/1486]	Time 0.019 (0.022)	Data 0.009 (0.011)	Loss 0.0090 (0.0227)	F1 nan 	
Epoch: [0][1050/1486]	Time 0.019 (0.022)	Data 0.009 (0.011)	Loss 0.0089 (0.0225)	F1 nan 	
Epoch: [0][1060/1486]	Time 0.019 (0.022)	Data 0.009 (0.011)	Loss 0.0092 (0.0224)	F1 nan 	
Epoch: [0][107

<ipython-input-55-06c7b316185a>:79: RuntimeWarning: invalid value encountered in double_scalars
  return intersect_size(yhatmic, ymic, 0) / yhatmic.sum(axis=0)


...

Epoch: [32][1260/1486]	Time 0.019 (0.021)	Data 0.009 (0.011)	Loss 0.0048 (0.0060)	F1 0.380 	
Epoch: [32][1270/1486]	Time 0.019 (0.021)	Data 0.009 (0.011)	Loss 0.0064 (0.0060)	F1 0.301 	
Epoch: [32][1280/1486]	Time 0.018 (0.021)	Data 0.009 (0.011)	Loss 0.0060 (0.0060)	F1 0.277 	
Epoch: [32][1290/1486]	Time 0.020 (0.021)	Data 0.010 (0.011)	Loss 0.0058 (0.0060)	F1 0.314 	
Epoch: [32][1300/1486]	Time 0.018 (0.021)	Data 0.009 (0.011)	Loss 0.0063 (0.0060)	F1 0.273 	
Epoch: [32][1310/1486]	Time 0.019 (0.021)	Data 0.009 (0.011)	Loss 0.0056 (0.0060)	F1 0.327 	
Epoch: [32][1320/1486]	Time 0.021 (0.021)	Data 0.011 (0.011)	Loss 0.0064 (0.0060)	F1 0.334 	
Epoch: [32][1330/1486]	Time 0.020 (0.021)	Data 0.010 (0.011)	Loss 0.0060 (0.0060)	F1 0.287 	
Epoch: [32][1340/1486]	Time 0.019 (0.021)	Data 0.010 (0.011)	Loss 0.0057 (0.0060)	F1 0.398 	
Epoch: [32][1350/1486]	Time 0.022 (0.021)	Data 0.012 (0.011)	Loss 0.0059 (0.0060)	F1 0.296 	
Epoch: [32][1360/1486]	Time 0.019 (0.021)	Data 0.009 (0.011)	Loss 0.00

Epoch: [33][370/1486]	Time 0.021 (0.028)	Data 0.012 (0.018)	Loss 0.0061 (0.0060)	F1 0.351 	
Epoch: [33][380/1486]	Time 0.022 (0.028)	Data 0.012 (0.018)	Loss 0.0066 (0.0060)	F1 0.314 	
Epoch: [33][390/1486]	Time 0.022 (0.028)	Data 0.012 (0.018)	Loss 0.0061 (0.0060)	F1 0.294 	
Epoch: [33][400/1486]	Time 0.022 (0.028)	Data 0.012 (0.018)	Loss 0.0056 (0.0060)	F1 0.288 	
Epoch: [33][410/1486]	Time 0.021 (0.028)	Data 0.011 (0.018)	Loss 0.0060 (0.0060)	F1 0.315 	
Epoch: [33][420/1486]	Time 0.021 (0.027)	Data 0.011 (0.018)	Loss 0.0059 (0.0060)	F1 0.319 	
Epoch: [33][430/1486]	Time 0.023 (0.027)	Data 0.012 (0.017)	Loss 0.0058 (0.0060)	F1 0.265 	
Epoch: [33][440/1486]	Time 0.023 (0.027)	Data 0.013 (0.017)	Loss 0.0065 (0.0060)	F1 0.232 	
Epoch: [33][450/1486]	Time 0.023 (0.027)	Data 0.013 (0.017)	Loss 0.0060 (0.0060)	F1 0.336 	
Epoch: [33][460/1486]	Time 0.022 (0.027)	Data 0.013 (0.017)	Loss 0.0059 (0.0060)	F1 0.278 	
Epoch: [33][470/1486]	Time 0.019 (0.027)	Data 0.009 (0.017)	Loss 0.0073 (0.0060)

Epoch: [33][1260/1486]	Time 0.020 (0.022)	Data 0.009 (0.012)	Loss 0.0056 (0.0060)	F1 0.266 	
Epoch: [33][1270/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.0061 (0.0060)	F1 0.273 	
Epoch: [33][1280/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.0064 (0.0060)	F1 0.283 	
Epoch: [33][1290/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.0063 (0.0060)	F1 0.315 	
Epoch: [33][1300/1486]	Time 0.022 (0.022)	Data 0.012 (0.012)	Loss 0.0051 (0.0060)	F1 0.307 	
Epoch: [33][1310/1486]	Time 0.018 (0.022)	Data 0.009 (0.012)	Loss 0.0056 (0.0060)	F1 0.329 	
Epoch: [33][1320/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.0060 (0.0060)	F1 0.306 	
Epoch: [33][1330/1486]	Time 0.018 (0.022)	Data 0.009 (0.012)	Loss 0.0056 (0.0060)	F1 0.265 	
Epoch: [33][1340/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.0052 (0.0060)	F1 0.296 	
Epoch: [33][1350/1486]	Time 0.018 (0.022)	Data 0.009 (0.012)	Loss 0.0062 (0.0060)	F1 0.215 	
Epoch: [33][1360/1486]	Time 0.019 (0.022)	Data 0.009 (0.012)	Loss 0.00

Epoch: [34][370/1486]	Time 0.021 (0.027)	Data 0.011 (0.018)	Loss 0.0047 (0.0060)	F1 0.358 	
Epoch: [34][380/1486]	Time 0.020 (0.027)	Data 0.010 (0.017)	Loss 0.0053 (0.0060)	F1 0.321 	
Epoch: [34][390/1486]	Time 0.020 (0.027)	Data 0.010 (0.017)	Loss 0.0058 (0.0060)	F1 0.294 	
Epoch: [34][400/1486]	Time 0.019 (0.027)	Data 0.009 (0.017)	Loss 0.0070 (0.0060)	F1 0.247 	
Epoch: [34][410/1486]	Time 0.019 (0.027)	Data 0.009 (0.017)	Loss 0.0066 (0.0060)	F1 0.348 	
Epoch: [34][420/1486]	Time 0.019 (0.026)	Data 0.009 (0.017)	Loss 0.0063 (0.0060)	F1 0.301 	
Epoch: [34][430/1486]	Time 0.019 (0.026)	Data 0.009 (0.017)	Loss 0.0070 (0.0060)	F1 0.314 	
Epoch: [34][440/1486]	Time 0.019 (0.026)	Data 0.009 (0.016)	Loss 0.0049 (0.0060)	F1 0.323 	
Epoch: [34][450/1486]	Time 0.019 (0.026)	Data 0.009 (0.016)	Loss 0.0058 (0.0060)	F1 0.338 	
Epoch: [34][460/1486]	Time 0.019 (0.026)	Data 0.009 (0.016)	Loss 0.0050 (0.0060)	F1 0.378 	
Epoch: [34][470/1486]	Time 0.019 (0.026)	Data 0.009 (0.016)	Loss 0.0050 (0.0060)

Epoch: [34][1270/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0058 (0.0060)	F1 0.356 	
Epoch: [34][1280/1486]	Time 0.018 (0.021)	Data 0.009 (0.012)	Loss 0.0063 (0.0060)	F1 0.367 	
Epoch: [34][1290/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0065 (0.0060)	F1 0.326 	
Epoch: [34][1300/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0061 (0.0060)	F1 0.258 	
Epoch: [34][1310/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0066 (0.0060)	F1 0.302 	
Epoch: [34][1320/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0051 (0.0060)	F1 0.343 	
Epoch: [34][1330/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0067 (0.0060)	F1 0.347 	
Epoch: [34][1340/1486]	Time 0.019 (0.021)	Data 0.009 (0.012)	Loss 0.0055 (0.0060)	F1 0.271 	
Epoch: [34][1350/1486]	Time 0.020 (0.021)	Data 0.011 (0.012)	Loss 0.0062 (0.0060)	F1 0.270 	
Epoch: [34][1360/1486]	Time 0.021 (0.021)	Data 0.010 (0.012)	Loss 0.0047 (0.0060)	F1 0.317 	
Epoch: [34][1370/1486]	Time 0.020 (0.021)	Data 0.010 (0.012)	Loss 0.00

## That's it! 

For this portion of the project, I had to spend alot of time trying to adapt the code to my liking and run accordingly. I didnt implement them from scratch due to the interest of time so it is alot of stitching here and there.